## Genetic Algorithm GUI tutorial

A python implementation of real-valued, genetic algorithm for solving hyperparameter optimization problems.

We recommend going through the Hyperparameter Optimization using `chemml.optimization.GeneticAlgorithm` section of the documentation to get a better understanding of the parameters required to run the Genetic Algorithm. In this tutorial we showcase the procedure to optimize the hyperparameters of a MLPRegressor model. 

We use a sample dataset from the ChemML library which has the SMILES codes and the HOMO energies (eV). We represent the data using Morgan Fingerprints (represented and a vector using 1024 bits). We split the data using a 90:10 (training data: testing data) split. We predict the HOMO energies of the test data set using the MLPRegressor model with optmized hyperparameters.

Five text files containing python code are required to run the Genetic Algorithm using the GUI. 

Text files required:
 - evaluate
 - error_metric
 - single_obj
 - space
 - test_hyperparameters

### evaluate 

The file `ga_eval.txt` contains python code which evaluates every individual (tuple of hyperparameters) and yields the results of the error metric for each generation. Once model type is selected in the Wrapper parameters section of the GUI, the model is defined in this section code. For each generation, the hyperparemeters of the model are set and the model is passed to the objective function (`single_obj`) which evaluates the model. 

The hyperparameter optimization process can be a time consuming one. Hence, for our convinience, we use a temporary file to guage and print the progress of the iterations. This is done using this section of the code: 

    #count iterations of GA
    count=open("tmp.txt", "a")
    count.write("GA search iteration in process... \n")
    count.close()
    file = open("tmp.txt","r")
    Counter = 0
    # Reading number of lines from file
    Content = file.read()
    CoList = Content.split("\n")
    for i in CoList:
        if i:
            Counter += 1
    print("GA search iteration in process... ",Counter)


_Note: The `tmp.txt` file is deleted once the GA search is completed_


**`ga_eval.txt` has the following python code:**

    def ga_eval(indi):
        
        layers = [indi[i] for i in range(2,5) if indi[i] != 0]
        #count iterations of GA
        count=open("tmp.txt", "a")
        count.write("GA search iteration in process... \n")
        count.close()
        file = open("tmp.txt","r")
        Counter = 0
        # Reading number of lines from file
        Content = file.read()
        CoList = Content.split("\n")
        for i in CoList:
            if i:
                Counter += 1
        print("GA search iteration in process... ",Counter)
        mlp = MLPRegressor(alpha=np.exp(indi[0]), activation=indi[1], 
        hidden_layer_sizes=tuple(layers),learning_rate='invscaling', max_iter=10,early_stopping=True)
        ga_search = single_obj(mlp=mlp, x=X.values, y=Y.values,n_splits=n_splits)
        f=open("GA.txt", "a")
        f.write("%f %s %d %d %d %f \n" %(float(np.exp(indi[0])), str(indi[1]), int(indi[2]), int(indi[3]), 
        int(indi[4]),float(ga_search)))
        f.close()
        return ga_search

### error_metric

The file `error_metric.txt` contains python code which returns the user defined error metric score (in this case Mean Absolute Error) for the data. The error metric returned in this function will define the criteria on which the "best model" is evaluated.

    def error_metric(y_true,y_pred):
        y_true = np.asarray(y_true)
        y_pred = np.asarray(y_pred)
        ndata = len(y_true)
        y_mean = np.mean(y_true)
        e = y_true - y_pred
        ae = np.absolute(e)
        se = np.square(e)
        var = np.mean(np.square(y_true - y_mean))
        MAE = np.mean(ae)
        return MAE

### single_obj

The file `single_obj.txt` contains python code which fits the model to the dataset using the hyperparameters defined in the `ga_eval` function. The training data is split into `n-splits` (defined by the user) and an error metric for each `fold` is obtained. 

This function returns the mean error_metric score of the `Kfold`(s) specified.


**`single_obj.txt` has the following python code:**

    def single_obj(mlp, x, y, n_splits=n_splits):
        n_splits=n_splits
        kf = KFold(n_splits)                    # cross validation based on Kfold (creates 5 validation train-test sets)
        accuracy_kfold = []
        for training, testing in kf.split(x):
            mlp.fit(x[training], y[training])
            y_pred = mlp.predict(x[testing])
            y_pred, y_act =y_pred.reshape(-1,1), y[testing].reshape(-1,1)
            model_accuracy=mae(y_act,y_pred)                             # evaluation metric:  mae
            accuracy_kfold.append(model_accuracy)                         # creates list of accuracies for each fold
        #print("def single_obj - completed")
        return np.mean(accuracy_kfold)

### space

The file `space.txt` contains python code which defines the space variable.

    space = ({'alpha': {'uniform': [np.log(0.0001), np.log(0.1)], 'mutation': [0, 1]}},{'activation': {'choice': ['identity', 'logistic', 'tanh', 'relu']}},{'neurons1':  {'choice': range(0,220,20)}},{'neurons2':  {'choice': range(0,220,20)}},{'neurons3':  {'choice': range(0,220,20)}})

### test_hyperparameters

The file `test_hyperparameters.txt` contains python code which fits the model, having the best hyperparameters obtained using the GA, to the training dataset. The model is used to predict the values of the testing data set. The function returns a error metric score (in this case MAE) of the predicted values and actual values. 

**`test_hyperparameters.txt` has the following python code:**

    def test_hyp(mlp, x, y, xtest, ytest):                                          
        mlp.fit(x, y)
        ypred = mlp.predict(xtest)
        acc=mae(ytest,ypred)
        # print(" test_hyp completed ")
        return np.mean(acc)

In [1]:
from chemml.wrapper.notebook import ChemMLNotebook
ui = ChemMLNotebook()

Accordion(children=(VBox(children=(Label(value='Choose how to start:', layout=Layout(width='50%')), Tab(childr…

The computation graph will be displayed here:


Image(value=b'')

Image(value=b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x032\x00\x00\x02\x7f\x08\x06\x00\x00\x00\xa3\x84\xe6…


The ChemML Wrapper's config file has been successfully saved ...
    config file name: chemML_config.txt
    current directory: /mnt/c/Aatish/UB/Mr. Hachmann/master_chemml_wrapper_v2
    what's next? run the ChemML Wrapper using the config file with the following codes:
        >>> from chemml.wrapper.engine import run
        >>> run(INPUT_FILE = 'path_to_the_config_file', OUTPUT_DIRECTORY = 'CMLWrapper_out')
... you can also create a python script of the above codes and run it on any cluster that ChemML is installed.


In [3]:
from chemml.wrapper.engine import run
run(INPUT_FILE = '/mnt/c/Aatish/UB/Mr. Hachmann/master_chemml_wrapper_v2/chemML_config.txt', OUTPUT_DIRECTORY = 'ga_out')

Thu Oct 21 13:15:40 2021

parsing the input file: /mnt/c/Aatish/UB/Mr. Hachmann/master_chemml_wrapper_v2/chemML_config.txt ...

1   Task: (Input,datasets)
        <<<<<<<
        host = chemml
        function = load_cep_homo
        >>>>>>>
        smiles -> send (id=0)
        homo -> send (id=4)
         :nothing to receive:
        
2   Task: (Output,file)
        <<<<<<<
        host = chemml
        function = SaveFile
        format = smi
        header = False
        filename = smiles
        >>>>>>>
        filepath -> send (id=1)
        df <- recv (id=0)
        
3   Task: (Represent,molecular descriptors)
        <<<<<<<
        host = chemml
        function = RDKitFingerprint
        >>>>>>>
        df -> send (id=2)
        df -> send (id=3)
        molfile <- recv (id=1)
        
4   Task: (Output,file)
        <<<<<<<
        host = chemml
        function = SaveFile
        filename = fps_rdkfp
        >>>>>>>
         :nothing to send:
        df <- recv (id=2)
    